In [1]:
# Load in one of the tables
df1 = spark.sql("select * from default.video_games_5")
df2 = spark.sql("select * from default.home_and_kitchen_5_small")
df3 = spark.sql("select * from default.books_5_small")

#data = df1
#data = df1.union(df2)
data = df1.union(df2).union(df3)

data = data.sample(False, 0.01, seed=0)

data = data.cache()

print((data.count(), len(data.columns)))

(34854, 12)

In [2]:
# Check nulls
from pyspark.sql.functions import isnull, when, count, col
nacounts = data.select([count(when(isnull(c), c)).alias(c) for c in data.columns]).toPandas()
nacounts

reviewID 
 overall 
 vote 
 verified 
 reviewTime 
 reviewerID 
 asin 
 reviewerName 
 reviewText 
 summary 
 unixReviewTime 
 label 
 
 
 
 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 2 
 0 
 2 
 0 
 0

In [3]:
data = data.dropna(thresh=2,subset=('summary','reviewerName'))

In [4]:
data = data.dropDuplicates(['reviewerID', 'asin'])

In [5]:
import pyspark.sql.functions as f
from pyspark.sql.types import FloatType

# Re-balancing (weighting) of records to be used in the logistic loss objective function
numPositives = data.filter(data["label"] == 1).count()
datasetSize = data.count()
balancingRatio = (datasetSize - numPositives) / datasetSize
print("numPositives   = {}".format(numPositives))
print("datasetSize    = {}".format(datasetSize))
print("balancingRatio = {}".format(balancingRatio))

def calculateWeights(d):
    if d == 1.0:
      return 1 * balancingRatio
    else:
      return 1 * (1.0 - balancingRatio)
    
udfcalculateWeights = f.udf(calculateWeights, FloatType())
    
data = data.withColumn("classWeightCol", udfcalculateWeights(data["label"]))
data.show(5)

numPositives = 6243
datasetSize = 34809
balancingRatio = 0.8206498319400155
+--------+-------+----+--------+-----------+--------------+----------+--------------+--------------------+--------------------+--------------+-----+--------------+
reviewID|overall|vote|verified| reviewTime| reviewerID| asin| reviewerName| reviewText| summary|unixReviewTime|label|classWeightCol|
+--------+-------+----+--------+-----------+--------------+----------+--------------+--------------------+--------------------+--------------+-----+--------------+
 560095| 5.0| 0| true| 10 8, 2013|A1072FC8PJMATW|0060175982|Chantal Hinton|I was pleased wit...|Great Book-Great ...| 1381190400| 0| 0.17935017|
 1798521| 5.0| 0| true| 03 1, 2016|A10EZ0086VK1GJ|B002IA0PHS| Double M|My upteenth 4 cup...| Five Stars| 1456790400| 0| 0.17935017|
 1471981| 5.0| 0| true|09 14, 2016|A11ARNBFLS7R7P|B001EU9UTM| jack|fabulous product....|tried it as soon ...| 1473811200| 0| 0.17935017|
 1035922| 3.0| 10| true|08 31, 2016|A120RUP3KGFNLJ|B00160NKVE| MTSTEEL|To start be prepa...|You pay for what ...| 1472601600| 1| 0.8206498|
 135365| 3.0| 0| true|06 14, 2014|A12I9B1JWWDV9I|B00008CM69| Beez|Pot is nice looki...| Ok replacement| 1402704000| 0| 0.17935017|
+--------+-------+----+--------+-----------+--------------+----------+--------------+--------------------+--------------------+--------------+-----+--------------+
only showing top 5 rows

In [6]:
display(data)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label classWeightCol 560095 5.0 0 true 10 8, 2013 A1072FC8PJMATW 0060175982 Chantal Hinton I was pleased with the service and quality of the book. It is a great book for anyone who gets divorced or loses a loved one. Great Book-Great Service 1381190400 0 0.17935017 1798521 5.0 0 true 03 1, 2016 A10EZ0086VK1GJ B002IA0PHS Double M My upteenth 4 cup over the years. Wish they would make the blade stronger. Five Stars 1456790400 0 0.17935017 1471981 5.0 0 true 09 14, 2016 A11ARNBFLS7R7P B001EU9UTM jack fabulous product. tried it as soon as we got it great expresso.mr coffee reliability seems to be there tried it as soon as we got it great expresso. mr coffee reliability seems to be there 1473811200 0 0.17935017 1035922 3.0 10 true 08 31, 2016 A120RUP3KGFNLJ B00160NKVE MTSTEEL To start be prepared to take some time to put it together, I was not timing it but it took me roughly about 1 hour to put it together. The directions were not the best and there is a lot of parts for this to put it together. The top and bottom doors didn't align right and were off, I got the bottom aligned but no matter what I did I couldn't get the top to align right so there is gaps in the top. I believe it's just the curio itself and whatever wood they used. The old saying you pay for what you get applies here. For the money it's okay not the best and not the worst. I was looking to complement my other Curio -(see the pictures, the last two) as you can see no gaps. I will keep looking for a quality used Curio to replace this. You pay for what you get 1472601600 1 0.8206498 135365 3.0 0 true 06 14, 2014 A12I9B1JWWDV9I B00008CM69 Beez Pot is nice looking. I do not like the lid at all. Very cheap looking with sharp edges. Pot itself is nice but lid is thin. Cleans up nice. I have always been happy with Cuisinart products. This must be a cheapie. Ok replacement 1402704000 0 0.17935017 706152 5.0 0 true 02 3, 2017 A12JTIKL4N0H3V B000NBWRU2 puppy9 this is one of my favorite products. i am Paleo and i use this with my Ghee, coconut oil and olive oil to first brown meat half way, then add an enormous amount of frozen veggies. the pan is really a great size and comes up far enough on the sides that i don't have to use a splatter screen or purchase a lid. we have also used on side of it for eggs and if we ate sausages with it i am sure they would go on the other side of the pan it has a handle which makes it so easy to maneuver and control use for paleo eating brown meat half way then add huge amount of frozen veggies with Ghee and cocount oil love this so much 1486080000 0 0.17935017 62391 4.0 0 true 07 12, 2016 A172359Z97CWYN B0006ZJPSC A.Bren Much longer than I thought it was going to be. Good story, fun game. I played it all the way through. Good Stuff. 1468281600 0 0.17935017 1761596 5.0 0 true 01 8, 2011 A17AKJBQX3JOT6 B002CM8U06 Sue Sew I bought this because I started breadmaking and wanted to be more accurate by measuring by weight. Also thought it would come in handy to measure serving sizes on things like snacks to get a better idea of how many calories rather than figuring one sixth of a bag when they say there are six servings per bag, etc. Works good and is just the right size. Not too complicated or fussy. Just what I was looking for 1294444800 0 0.17935017 169843 4.0 0 true 05 2, 2014 A17SDM1OMZ697H 0007196997 sabner I love Dean Koontz because he doesn't bounce from past to future a lot like Steven King. His quality of writing is great in every book of this series. You'll love this series. Koontz is always great. 1398988800 0 0.17935017 620679 5.0 0 true 01 5, 2009 A180AIG9XAXU9B B000J4LCS6 Glinda My 89 y.o. Dad suffers from Parkinsons. Since he doesn't swallow as often as non afflicted he is tormented with a phlegm build up during the night. This warm mist vaporizer made a significant improvement in his breathing comfort as well as speaking ability

In [7]:
from sparknlp.base import*
from sparknlp.annotator import *
from nltk.corpus import *
from sparknlp.annotator import *

from sparknlp.base import DocumentAssembler, Finisher
from pyspark.ml.feature import StringIndexer, VectorIndexer
from sparknlp.annotator import Tokenizer, Normalizer, StopWordsCleaner, Stemmer
from pyspark.ml.classification import MultilayerPerceptronClassifier, NaiveBayes, GBTClassifier, DecisionTreeClassifier

from pyspark.ml import Pipeline
from pyspark.ml.feature import CountVectorizer, HashingTF, IDF, StringIndexer, SQLTransformer, IndexToString, VectorAssembler
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier

# convert text column to spark nlp document
document_assembler = DocumentAssembler() \
    .setInputCol("reviewText") \
    .setOutputCol("document")


# convert document to array of tokens
tokenizer = Tokenizer() \
  .setInputCols(["document"]) \
  .setOutputCol("token")
 
# clean tokens 
normalizer = Normalizer() \
    .setInputCols(["token"]) \
    .setOutputCol("normalized")

#lemmatizer = LemmatizerModel.pretrained() \
 #    .setInputCols(['normalized']) \
  #   .setOutputCol('lemmatized')

# remove stopwords
stopwords_cleaner = StopWordsCleaner()\
      .setInputCols("normalized")\
      .setOutputCol("cleanTokens")\
      .setCaseSensitive(False)

# stems tokens to bring it to root form
stemmer = Stemmer() \
    .setInputCols(["cleanTokens"]) \
    .setOutputCol("stem")

# Convert custom document structure to array of tokens.
finisher = Finisher() \
    .setInputCols(["stem"]) \
    .setOutputCols(["token_features"]) \
    .setOutputAsArray(True) \
    .setCleanAnnotations(False)

# Generate Term Frequency
tf = CountVectorizer(inputCol="token_features", outputCol="rawFeatures", vocabSize=10000, minTF=1, minDF=50, maxDF=0.40)

# Generate Inverse Document Frequency weighting
idf = IDF(inputCol="rawFeatures", outputCol="idfFeatures", minDocFreq=5)

# Combine all features into one final "features" column
assembler = VectorAssembler(inputCols=["overall", "verified",  "idfFeatures"], outputCol="features")

# Index labels, adding metadata to the label column.
#labelIndexer = StringIndexer(inputCol="label", outputCol="indexedLabel")

# Automatically identify categorical features, and index them.
# Set maxCategories so features with > 4 distinct values are treated as continuous.
#featureIndexer = VectorIndexer(inputCol="features", outputCol="indexedFeatures", maxCategories=4, handleInvalid="skip")

layers = [2337, 10, 5, 2]
# Machine Learning Algorithm
#ml_alg  = LogisticRegression(maxIter=10, regParam=0.3, elasticNetParam=0.0)
#ml_alg  = RandomForestClassifier(numTrees=100).setLabelCol("label").setFeaturesCol("features")
#VERY POOR ON TEST DATA

ml_alg1=MultilayerPerceptronClassifier(maxIter=100, layers=layers, seed=1234).setLabelCol("label").setFeaturesCol("features")
ml_alg2=NaiveBayes(smoothing=1.0, modelType="multinomial", weightCol="classWeightCol")
#NB: 0.6401
ml_alg3=LogisticRegression(maxIter=10, regParam=0.3, elasticNetParam=0.0).setWeightCol("classWeightCol").setLabelCol("label").setFeaturesCol("features") 
#LR: 0.63
#ml_alg=GBTClassifier(labelCol="indexedLabel", featuresCol="indexedFeatures", maxIter=10, seed=0)
#ml_alg = DecisionTreeClassifier(labelCol="indexedLabel", featuresCol="indexedFeatures",impurity="entropy", seed=1)


nlp_pipeline1 = Pipeline(
    stages=[document_assembler, 
            tokenizer,
            normalizer,
            #lemmatizer,
            stopwords_cleaner, 
            stemmer, 
            finisher,
            tf,
            idf,
            assembler,
            #labelIndexer,
            #featureIndexer,
            ml_alg1])

nlp_pipeline2 = Pipeline(
    stages=[document_assembler, 
            tokenizer,
            normalizer,
            #lemmatizer,
            stopwords_cleaner, 
            stemmer, 
            finisher,
            tf,
            idf,
            assembler,
            #labelIndexer,
            #featureIndexer,
            ml_alg2])

nlp_pipeline3 = Pipeline(
    stages=[document_assembler, 
            tokenizer,
            normalizer,
            #lemmatizer,
            stopwords_cleaner, 
            stemmer, 
            finisher,
            tf,
            idf,
            assembler,
            #labelIndexer,
            #featureIndexer,
            ml_alg3])



In [8]:
(trainingData, testData) = data.randomSplit([0.8, 0.2], seed = 7)

In [9]:
pipeline_model_nn = nlp_pipeline1.fit(trainingData)

In [10]:
pipeline_model_nb = nlp_pipeline2.fit(trainingData)

In [11]:
pipeline_model_lr = nlp_pipeline3.fit(trainingData)

In [12]:
predictions_nn =  pipeline_model_nn.transform(testData)
display(predictions_nn)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label classWeightCol document token normalized cleanTokens stem token_features rawFeatures idfFeatures features rawPrediction probability prediction 15036 5.0 0 true 03 6, 2013 A1H5I60LTGM0X0 0002185385 Taylor a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more... a very handy little red book on golf 1362528000 0 0.17935017 List(List(document, 0, 153, a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 63, 63, ., Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 133, 133, ., Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List()), List(token, 151, 153, ..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List())) List(List(token, 7, 11, handy, Map(sentence -> 0), List()), List(tok

In [13]:
predictions_nb =  pipeline_model_nb.transform(testData)
display(predictions_nb)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label classWeightCol document token normalized cleanTokens stem token_features rawFeatures idfFeatures features rawPrediction probability prediction 15036 5.0 0 true 03 6, 2013 A1H5I60LTGM0X0 0002185385 Taylor a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more... a very handy little red book on golf 1362528000 0 0.17935017 List(List(document, 0, 153, a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 63, 63, ., Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 133, 133, ., Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List()), List(token, 151, 153, ..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List())) List(List(token, 7, 11, handy, Map(sentence -> 0), List()), List(tok

In [14]:
predictions_lr =  pipeline_model_lr.transform(testData)
display(predictions_lr)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label classWeightCol document token normalized cleanTokens stem token_features rawFeatures idfFeatures features rawPrediction probability prediction 15036 5.0 0 true 03 6, 2013 A1H5I60LTGM0X0 0002185385 Taylor a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more... a very handy little red book on golf 1362528000 0 0.17935017 List(List(document, 0, 153, a very handy and insightful guide on all facets of golf playing. i really enjoyed this fine book which has helped my game drasticaly. hacking no more..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 63, 63, ., Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 133, 133, ., Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List()), List(token, 151, 153, ..., Map(sentence -> 0), List())) List(List(token, 0, 0, a, Map(sentence -> 0), List()), List(token, 2, 5, very, Map(sentence -> 0), List()), List(token, 7, 11, handy, Map(sentence -> 0), List()), List(token, 13, 15, and, Map(sentence -> 0), List()), List(token, 17, 26, insightful, Map(sentence -> 0), List()), List(token, 28, 32, guide, Map(sentence -> 0), List()), List(token, 34, 35, on, Map(sentence -> 0), List()), List(token, 37, 39, all, Map(sentence -> 0), List()), List(token, 41, 46, facets, Map(sentence -> 0), List()), List(token, 48, 49, of, Map(sentence -> 0), List()), List(token, 51, 54, golf, Map(sentence -> 0), List()), List(token, 56, 62, playing, Map(sentence -> 0), List()), List(token, 66, 66, i, Map(sentence -> 0), List()), List(token, 68, 73, really, Map(sentence -> 0), List()), List(token, 75, 81, enjoyed, Map(sentence -> 0), List()), List(token, 83, 86, this, Map(sentence -> 0), List()), List(token, 88, 91, fine, Map(sentence -> 0), List()), List(token, 93, 96, book, Map(sentence -> 0), List()), List(token, 98, 102, which, Map(sentence -> 0), List()), List(token, 104, 106, has, Map(sentence -> 0), List()), List(token, 108, 113, helped, Map(sentence -> 0), List()), List(token, 115, 116, my, Map(sentence -> 0), List()), List(token, 118, 121, game, Map(sentence -> 0), List()), List(token, 123, 132, drasticaly, Map(sentence -> 0), List()), List(token, 136, 142, hacking, Map(sentence -> 0), List()), List(token, 144, 145, no, Map(sentence -> 0), List()), List(token, 147, 150, more, Map(sentence -> 0), List())) List(List(token, 7, 11, handy, Map(sentence -> 0), List()), List(tok

In [15]:
print("NN  comparison of Label and Prediction")

predictions_nn.groupBy("label").count().show()
predictions_nn.groupBy("prediction").count().show()

NN comparison of Label and Prediction
+-----+-----+
label|count|
+-----+-----+
 1| 1266|
 0| 5745|
+-----+-----+

+----------+-----+
prediction|count|
+----------+-----+
 0.0| 5795|
 1.0| 1216|
+----------+-----+

In [16]:
print("NB  comparison of Label and Prediction")

predictions_nb.groupBy("label").count().show()
predictions_nb.groupBy("prediction").count().show()

NB comparison of Label and Prediction
+-----+-----+
label|count|
+-----+-----+
 1| 1266|
 0| 5745|
+-----+-----+

+----------+-----+
prediction|count|
+----------+-----+
 0.0| 5733|
 1.0| 1278|
+----------+-----+

In [17]:
print("LR  comparison of Label and Prediction")

predictions_lr.groupBy("label").count().show()
predictions_lr.groupBy("prediction").count().show()

LR comparison of Label and Prediction
+-----+-----+
label|count|
+-----+-----+
 1| 1266|
 0| 5745|
+-----+-----+

+----------+-----+
prediction|count|
+----------+-----+
 0.0| 5423|
 1.0| 1588|
+----------+-----+

In [18]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator, MulticlassClassificationEvaluator

acc_evaluator_nn = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
pre_evaluator_nn = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="weightedPrecision")
rec_evaluator_nn = MulticlassClassificationEvaluator(metricName="weightedRecall")
pr_evaluator_nn = BinaryClassificationEvaluator(metricName="areaUnderPR")
auc_evaluator_nn = BinaryClassificationEvaluator(metricName="areaUnderROC")

print("Test Accuracy       = %g" % (acc_evaluator_nn.evaluate(predictions_nn)))
print("Test Precision      = %g" % (pre_evaluator_nn.evaluate(predictions_nn)))
print("Test Recall         = %g" % (rec_evaluator_nn.evaluate(predictions_nn)))
print("Test areaUnderPR    = %g" % (pr_evaluator_nn.evaluate(predictions_nn)))
print("Test areaUnderROC   = %g" % (auc_evaluator_nn.evaluate(predictions_nn)))

Test Accuracy = 0.800599
Test Precision = 0.797537
Test Recall = 0.800599
Test areaUnderPR = 0.365529
Test areaUnderROC = 0.68533

In [19]:
acc_evaluator_nb = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
pre_evaluator_nb = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="weightedPrecision")
rec_evaluator_nb = MulticlassClassificationEvaluator(metricName="weightedRecall")
pr_evaluator_nb  = BinaryClassificationEvaluator(metricName="areaUnderPR")
auc_evaluator_nb = BinaryClassificationEvaluator(metricName="areaUnderROC")

print("Test Accuracy       = %g" % (acc_evaluator_nb.evaluate(predictions_nb)))
print("Test Precision      = %g" % (pre_evaluator_nb.evaluate(predictions_nb)))
print("Test Recall         = %g" % (rec_evaluator_nb.evaluate(predictions_nb)))
print("Test areaUnderPR    = %g" % (pr_evaluator_nb.evaluate(predictions_nb)))
print("Test areaUnderROC   = %g" % (auc_evaluator_nb.evaluate(predictions_nb)))

Test Accuracy = 0.802596
Test Precision = 0.803326
Test Recall = 0.802596
Test areaUnderPR = 0.106296
Test areaUnderROC = 0.178402

In [20]:
acc_evaluator_lr = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
pre_evaluator_lr = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="weightedPrecision")
rec_evaluator_lr = MulticlassClassificationEvaluator(metricName="weightedRecall")
pr_evaluator_lr  = BinaryClassificationEvaluator(metricName="areaUnderPR")
auc_evaluator_lr = BinaryClassificationEvaluator(metricName="areaUnderROC")

print("Test Accuracy       = %g" % (acc_evaluator_lr.evaluate(predictions_lr)))
print("Test Precision      = %g" % (pre_evaluator_lr.evaluate(predictions_lr)))
print("Test Recall         = %g" % (rec_evaluator_lr.evaluate(predictions_lr)))
print("Test areaUnderPR    = %g" % (pr_evaluator_lr.evaluate(predictions_lr)))
print("Test areaUnderROC   = %g" % (auc_evaluator_lr.evaluate(predictions_lr)))

Test Accuracy = 0.816289
Test Precision = 0.83548
Test Recall = 0.816289
Test areaUnderPR = 0.521268
Test areaUnderROC = 0.831142

In [21]:
# Reading Kaggle data from Database
Kaggle_test = spark.sql("select * from default.reviews_kaggle")

In [22]:
display(Kaggle_test)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime 67000000 3 true 05 16, 2012 A3IXM075VM1P9T B007JYB3O2 nachtik I would say these were 5 regular short stories, nothing exceptional or to be worth recommending to others. I didn't read any full book or novel from this author, maybe that would be much better reading. But these short stories wouldn't convince me to go for it. average reading 1.3371264E9 67000001 5 true 12 25, 2012 A3LGZ7A3WSV3JJ 985719745 MSP WOW, DROPPIN DIMES 2 was SOOOOOOO GOOD, BETTER than pt. 1. A JUICY TALE of BETRAYAL, JEALOUSY, OBSESSION, a FEW CRAZY EX'S, TRUE LOVE, CONSEQUENCES to ACTIONS, PATERNITY TESTS, DRAMA, DRAMA, DRAMA, and MORE. ISIS was SOOOOOO SHIESTY. Although MAR'KEL made POOR CHOICES, with 3 POSSIBLE BABY DADDIES, I RESPECTED HER HONESTY. All THREE MEN TRULY LOVED HER, and the BABY. ONE had a FEW ISSUES. Who is the BABY DADDY? Which man will MAR'KEL CHOOSE? or Will the CHOICE be MADE for HER? BUY THIS BOOK and FIND OUT. YOU WILL NOT BE DISAPPOINTED. I was ENGROSSED and INTRIGUED to the VERY END. The way it ENDED, I KNOW a pt. 3 is in the FUTURE. I will be on PINS and NEEDLES ANTICIPATING its RELEASE. CHLOE JE'NORE, TWO THUMBS UP....... WOW................. 1.3563936E9 67000002 5 true 09 18, 2012 A3BF5G7CJNIAG0 B002KXH7PQ C. S. DeMore You'll love the pattern for witches in this book--great fun to make wall hangings for friends and family--each one a little bit different--a Buggy Barn trademark. Grat to be able to use my points to get a deal on some of these books! Another Buggy Barn Delight 1.3479264E9 67000003 5 false 07 27, 2015 A2W41RTHSHYC4Q B011LXVWRO Light For the majority of persons Algarve means beach, sun and fun. However, the author shows us that there are more things to do in Algarve. Actually there are activities for every member of the family, either in group or individually. In this way, parents can visit a medieval castle (Castelo de Silves), board a ferry to go to Spain, play golf, etc. Young people can enjoy all kinds of water activities and surfing, have a pool party or go to the disco in the evening. Children can enjoy Aqualand, a truly fun water park. At the end of the book, the author lists the top 10 bars, top 5 markets, gay spots, top festivals, coffee shops, clubs, hostels, restaurants (vegetarian too), top 10 beaches, churches, parks, etc. The author includes links to the internet so you can get more information. Also, he includes links to maps to locate every site easily. This is a complete and practical guide book! This is a complete and practical guide book! 1.4379552E9 67000004 5 false 03 29, 2003 ACTBQZV1CJ9E8 9706061681 Richard Eastwood MI MEJOR AMIGO..QUE ESPANTO ! La chica adelgazaba ( mintiendo a sus padres con que estaba a dieta ) Era una nia buena, pero esta horrible enfermedad se convierte en una obsesion tan seria que las hace mentir para que no las obliguen a comer.. Por desgracia, cuando mi amigo Michael se dio cuenta, ya era demasiado tarde ! SEPULTAMOS A MAGGIE LA SEMANA PASADA, LUEGO DE UNA LUCHA DE TRES AOS ! ES VITAL INFORMARNOS Y ESTE LIBRO LO HACE... A TIEMPO ! LE ACABA DE SUCEDER A LA HIJA MAYOR DE 1.048896E9 67000005 5 true 04 22, 2014 A1RL0VMJVV8Q9N B00BDAIDQ4 Barbara270 This is a short story, yet beautifully written. The author wrote with the brilliance of Steinbeck. The story in itself was riveting and well told. Add to the wonderful story the description used, and you have yourself an unforgettable read. I will read more by this author for the beauty of the words he selects. If you are a student of the written word, you're going to love this story. Beautifully Written 1.3981248E9 67000006 5 false 08 18, 2015 A3GXIIUS36J8MC 1943892172 Jeri T. Ryan Gamma Rift by Kalli Lanford was a huge surprise to me. It seems to be the start of a new series and I am not sure if it is a debut novel or if this is an author just writing under a new pen name. IF this is a debut novel I have to admit I am totally 

In [23]:
predictions_nn2 =  pipeline_model_nn.transform(Kaggle_test)

In [24]:
predictions_nb2 =  pipeline_model_nb.transform(Kaggle_test)

In [25]:
predictions_lr2 =  pipeline_model_lr.transform(Kaggle_test)

In [26]:
pred1=predictions_nn2.select("reviewID","prediction").withColumnRenamed('prediction','prediction_nn')
display(pred1)

reviewID prediction_nn 67000000 0.0 67000001 0.0 67000002 0.0 67000003 0.0 67000004 0.0 67000005 0.0 67000006 0.0 67000007 0.0 67000008 0.0 67000009 1.0 67000010 0.0 67000011 1.0 67000012 0.0 67000013 0.0 67000014 0.0 67000015 0.0 67000016 0.0 67000017 0.0 67000018 0.0 67000019 0.0 67000020 0.0 67000021 0.0 67000022 0.0 67000023 0.0 67000024 0.0 67000025 0.0 67000026 0.0 67000027 0.0 67000028 1.0 67000029 0.0 67000030 0.0 67000031 0.0 67000032 1.0 67000033 0.0 67000034 1.0 67000035 1.0 67000036 1.0 67000037 0.0 67000038 0.0 67000039 1.0 67000040 0.0 67000041 1.0 67000042 0.0 67000043 0.0 67000044 0.0 67000045 1.0 67000046 0.0 67000047 1.0 67000048 0.0 67000049 0.0 67000050 0.0 67000051 1.0 67000052 1.0 67000053 0.0 67000054 1.0 67000055 0.0 67000056 0.0 67000057 1.0 67000058 0.0 67000059 1.0 67000060 1.0 67000061 0.0 67000062 0.0 67000063 0.0 67000064 0.0 67000065 0.0 67000066 1.0 67000067 0.0 67000068 0.0 67000069 0.0 67000070 0.0 67000071 0.0 67000072 0.0 67000073 0.0 67000074 1.0 67000075 0.0 67000076 0.0 67000077 0.0 67000078 1.0 67000079 0.0 67000080 0.0 67000081 1.0 67000082 0.0 67000083 0.0 67000084 0.0 67000085 1.0 67000086 0.0 67000087 0.0 67000088 0.0 67000089 0.0 67000090 0.0 67000091 0.0 67000092 0.0 67000093 1.0 67000094 0.0 67000095 1.0 67000096 0.0 67000097 1.0 67000098 0.0 67000099 0.0 67000100 1.0 67000101 1.0 67000102 0.0 67000103 1.0 67000104 0.0 67000105 0.0 67000106 0.0 67000107 0.0 67000108 0.0 67000109 0.0 67000110 0.0 67000111 0.0 67000112 0.0 67000113 0.0 67000114 0.0 67000115 0.0 67000116 0.0 67000117 1.0 67000118 0.0 67000119 0.0 67000120 1.0 67000121 0.0 67000122 1.0 67000123 0.0 67000124 0.0 67000125 0.0 67000126 0.0 67000127 0.0 67000128 0.0 67000129 1.0 67000130 0.0 67000131 1.0 67000132 0.0 67000133 0.0 67000134 0.0 67000135 1.0 67000136 0.0 67000137 0.0 67000138 0.0 67000139 0.0 67000140 0.0 67000141 0.0 67000142 0.0 67000143 0.0 67000144 1.0 67000145 1.0 67000146 1.0 67000147 0.0 67000148 1.0 67000149 1.0 67000150 0.0 67000151 1.0 67000152 0.0 67000153 1.0 67000154 0.0 67000155 0.0 67000156 1.0 67000157 0.0 67000158 0.0 67000159 0.0 67000160 0.0 67000161 1.0 67000162 0.0 67000163 0.0 67000164 0.0 67000165 0.0 67000166 0.0 67000167 0.0 67000168 1.0 67000169 1.0 67000170 0.0 67000171 0.0 67000172 0.0 67000173 0.0 67000174 1.0 67000175 0.0 67000176 0.0 67000177 0.0 67000178 1.0 67000179 0.0 67000180 0.0 67000181 0.0 67000182 0.0 67000183 0.0 67000184 0.0 67000185 0.0 67000186 0.0 67000187 0.0 67000188 1.0 67000189 0.0 67000190 0.0 67000191 0.0 67000192 1.0 67000193 0.0 67000194 1.0 67000195 0.0 67000196 0.0 67000197 0.0 67000198 0.0 67000199 0.0 67000200 1.0 67000201 1.0 67000202 0.0 67000203 0.0 67000204 1.0 67000205 0.0 67000206 1.0 67000207 0.0 67000208 0.0 67000209 0.0 67000210 0.0 67000211 0.0 67000212 1.0 67000213 1.0 67000214 0.0 67000215 0.0 67000216 0.0 67000217 0.0 67000218 1.0 67000219 0.0 67000220 0.0 67000221 0.0 67000222 1.0 67000223 0.0 67000224 1.0 67000225 0.0 67000226 0.0 67000227 0.0 67000228 0.0 67000229 0.0 67000230 1.0 67000231 0.0 67000232 0.0 67000233 0.0 67000234 0.0 67000235 0.0 67000236 0.0 67000237 1.0 67000238 0.0 67000239 0.0 67000240 0.0 67000241 0.0 67000242 0.0 67000243 1.0 67000244 0.0 67000245 0.0 67000246 0.0 67000247 1.0 67000248 0.0 67000249 0.0 67000250 0.0 67000251 0.0 67000252 0.0 67000253 0.0 67000254 0.0 67000255 0.0 67000256 0.0 67000257 0.0 67000258 0.0 67000259 0.0 67000260 0.0 67000261 0.0 67000262 0.0 67000263 0.0 67000264 0.0 67000265 0.0 67000266 0.0 67000267 1.0 67000268 0.0 67000269 0.0 67000270 0.0 67000271 1.0 67000272 1.0 67000273 0.0 67000274 0.0 67000275 0.0 67000276 1.0 67000277 0.0 67000278 0.0 67000279 0.0 67000280 1.0 67000281 0.0 67000282 0.0 67000283 1.0 67000284 0.0 67000285 1.0 67000286 0.0 67000287 1.0 67000288 0.0 67000289 0.0 67000290 0.0 67000291 0.0 67000292 0.0 67000293 1.0 67000294 0.0 67000295 0.0 67000296 1.0 67000297 0.0 67000298 0.0 67000299 1.0 67000300 0.0 67000301 1.0 67000302 0.0 67000303 0.0 67000304 0.0 67000305 0.0

In [27]:
pred2=predictions_nb2.select("reviewID","prediction").withColumnRenamed('prediction','prediction_nb')
display(pred2)

reviewID prediction_nb 67000000 0.0 67000001 0.0 67000002 0.0 67000003 1.0 67000004 0.0 67000005 0.0 67000006 1.0 67000007 0.0 67000008 0.0 67000009 1.0 67000010 0.0 67000011 0.0 67000012 0.0 67000013 1.0 67000014 0.0 67000015 0.0 67000016 1.0 67000017 0.0 67000018 1.0 67000019 0.0 67000020 0.0 67000021 0.0 67000022 1.0 67000023 0.0 67000024 0.0 67000025 0.0 67000026 0.0 67000027 1.0 67000028 1.0 67000029 1.0 67000030 0.0 67000031 0.0 67000032 1.0 67000033 1.0 67000034 1.0 67000035 0.0 67000036 0.0 67000037 0.0 67000038 0.0 67000039 1.0 67000040 0.0 67000041 1.0 67000042 0.0 67000043 0.0 67000044 0.0 67000045 1.0 67000046 0.0 67000047 1.0 67000048 1.0 67000049 0.0 67000050 0.0 67000051 1.0 67000052 1.0 67000053 0.0 67000054 0.0 67000055 0.0 67000056 1.0 67000057 1.0 67000058 0.0 67000059 1.0 67000060 1.0 67000061 1.0 67000062 0.0 67000063 0.0 67000064 0.0 67000065 0.0 67000066 1.0 67000067 0.0 67000068 0.0 67000069 0.0 67000070 0.0 67000071 0.0 67000072 0.0 67000073 0.0 67000074 1.0 67000075 0.0 67000076 0.0 67000077 1.0 67000078 0.0 67000079 0.0 67000080 0.0 67000081 0.0 67000082 0.0 67000083 1.0 67000084 0.0 67000085 1.0 67000086 0.0 67000087 0.0 67000088 0.0 67000089 0.0 67000090 1.0 67000091 0.0 67000092 1.0 67000093 1.0 67000094 1.0 67000095 0.0 67000096 0.0 67000097 1.0 67000098 1.0 67000099 0.0 67000100 1.0 67000101 0.0 67000102 0.0 67000103 0.0 67000104 0.0 67000105 0.0 67000106 0.0 67000107 0.0 67000108 0.0 67000109 1.0 67000110 1.0 67000111 0.0 67000112 0.0 67000113 0.0 67000114 0.0 67000115 1.0 67000116 0.0 67000117 1.0 67000118 1.0 67000119 0.0 67000120 1.0 67000121 0.0 67000122 1.0 67000123 0.0 67000124 1.0 67000125 0.0 67000126 1.0 67000127 1.0 67000128 0.0 67000129 1.0 67000130 0.0 67000131 1.0 67000132 1.0 67000133 1.0 67000134 0.0 67000135 1.0 67000136 1.0 67000137 0.0 67000138 0.0 67000139 1.0 67000140 1.0 67000141 1.0 67000142 1.0 67000143 1.0 67000144 1.0 67000145 0.0 67000146 1.0 67000147 1.0 67000148 1.0 67000149 1.0 67000150 0.0 67000151 1.0 67000152 0.0 67000153 1.0 67000154 0.0 67000155 1.0 67000156 0.0 67000157 1.0 67000158 0.0 67000159 0.0 67000160 0.0 67000161 0.0 67000162 0.0 67000163 0.0 67000164 1.0 67000165 0.0 67000166 0.0 67000167 0.0 67000168 1.0 67000169 1.0 67000170 0.0 67000171 0.0 67000172 1.0 67000173 0.0 67000174 1.0 67000175 0.0 67000176 0.0 67000177 0.0 67000178 1.0 67000179 1.0 67000180 0.0 67000181 0.0 67000182 0.0 67000183 1.0 67000184 0.0 67000185 0.0 67000186 0.0 67000187 0.0 67000188 1.0 67000189 0.0 67000190 0.0 67000191 0.0 67000192 0.0 67000193 0.0 67000194 1.0 67000195 0.0 67000196 0.0 67000197 0.0 67000198 1.0 67000199 1.0 67000200 1.0 67000201 1.0 67000202 1.0 67000203 0.0 67000204 1.0 67000205 0.0 67000206 1.0 67000207 1.0 67000208 0.0 67000209 0.0 67000210 1.0 67000211 0.0 67000212 0.0 67000213 1.0 67000214 1.0 67000215 0.0 67000216 0.0 67000217 1.0 67000218 1.0 67000219 0.0 67000220 0.0 67000221 1.0 67000222 1.0 67000223 0.0 67000224 1.0 67000225 0.0 67000226 0.0 67000227 1.0 67000228 0.0 67000229 0.0 67000230 1.0 67000231 0.0 67000232 0.0 67000233 0.0 67000234 0.0 67000235 0.0 67000236 0.0 67000237 0.0 67000238 0.0 67000239 0.0 67000240 1.0 67000241 0.0 67000242 1.0 67000243 1.0 67000244 0.0 67000245 1.0 67000246 0.0 67000247 1.0 67000248 0.0 67000249 0.0 67000250 1.0 67000251 0.0 67000252 0.0 67000253 1.0 67000254 0.0 67000255 0.0 67000256 0.0 67000257 0.0 67000258 1.0 67000259 0.0 67000260 0.0 67000261 0.0 67000262 1.0 67000263 0.0 67000264 1.0 67000265 1.0 67000266 0.0 67000267 1.0 67000268 0.0 67000269 0.0 67000270 0.0 67000271 1.0 67000272 0.0 67000273 0.0 67000274 1.0 67000275 0.0 67000276 0.0 67000277 0.0 67000278 1.0 67000279 1.0 67000280 1.0 67000281 0.0 67000282 0.0 67000283 1.0 67000284 1.0 67000285 1.0 67000286 0.0 67000287 1.0 67000288 0.0 67000289 1.0 67000290 0.0 67000291 0.0 67000292 0.0 67000293 1.0 67000294 1.0 67000295 1.0 67000296 1.0 67000297 0.0 67000298 0.0 67000299 1.0 67000300 0.0 67000301 1.0 67000302 0.0 67000303 1.0 67000304 0.0 67000305 0.0

In [28]:
pred3=predictions_lr2.select("reviewID","prediction").withColumnRenamed('prediction','prediction_lr')
display(pred3)

reviewID prediction_lr 67000000 0.0 67000001 0.0 67000002 0.0 67000003 1.0 67000004 0.0 67000005 0.0 67000006 1.0 67000007 0.0 67000008 0.0 67000009 1.0 67000010 0.0 67000011 1.0 67000012 0.0 67000013 1.0 67000014 0.0 67000015 0.0 67000016 1.0 67000017 0.0 67000018 0.0 67000019 0.0 67000020 0.0 67000021 0.0 67000022 0.0 67000023 0.0 67000024 0.0 67000025 0.0 67000026 0.0 67000027 1.0 67000028 1.0 67000029 0.0 67000030 0.0 67000031 0.0 67000032 0.0 67000033 0.0 67000034 1.0 67000035 0.0 67000036 1.0 67000037 0.0 67000038 0.0 67000039 1.0 67000040 0.0 67000041 1.0 67000042 0.0 67000043 0.0 67000044 1.0 67000045 1.0 67000046 0.0 67000047 1.0 67000048 0.0 67000049 0.0 67000050 0.0 67000051 1.0 67000052 1.0 67000053 0.0 67000054 0.0 67000055 0.0 67000056 1.0 67000057 1.0 67000058 0.0 67000059 1.0 67000060 1.0 67000061 1.0 67000062 0.0 67000063 0.0 67000064 0.0 67000065 0.0 67000066 1.0 67000067 0.0 67000068 0.0 67000069 0.0 67000070 0.0 67000071 0.0 67000072 0.0 67000073 0.0 67000074 1.0 67000075 0.0 67000076 0.0 67000077 1.0 67000078 0.0 67000079 0.0 67000080 0.0 67000081 0.0 67000082 0.0 67000083 1.0 67000084 0.0 67000085 1.0 67000086 0.0 67000087 0.0 67000088 0.0 67000089 0.0 67000090 0.0 67000091 0.0 67000092 0.0 67000093 1.0 67000094 1.0 67000095 0.0 67000096 1.0 67000097 1.0 67000098 1.0 67000099 0.0 67000100 1.0 67000101 1.0 67000102 0.0 67000103 0.0 67000104 0.0 67000105 0.0 67000106 0.0 67000107 0.0 67000108 0.0 67000109 0.0 67000110 1.0 67000111 0.0 67000112 0.0 67000113 0.0 67000114 0.0 67000115 0.0 67000116 0.0 67000117 1.0 67000118 0.0 67000119 0.0 67000120 1.0 67000121 0.0 67000122 1.0 67000123 0.0 67000124 0.0 67000125 0.0 67000126 1.0 67000127 0.0 67000128 0.0 67000129 1.0 67000130 0.0 67000131 1.0 67000132 0.0 67000133 0.0 67000134 0.0 67000135 1.0 67000136 1.0 67000137 0.0 67000138 0.0 67000139 0.0 67000140 0.0 67000141 1.0 67000142 0.0 67000143 1.0 67000144 1.0 67000145 1.0 67000146 1.0 67000147 1.0 67000148 1.0 67000149 1.0 67000150 0.0 67000151 1.0 67000152 0.0 67000153 1.0 67000154 0.0 67000155 0.0 67000156 1.0 67000157 0.0 67000158 1.0 67000159 0.0 67000160 0.0 67000161 1.0 67000162 0.0 67000163 0.0 67000164 1.0 67000165 0.0 67000166 0.0 67000167 0.0 67000168 1.0 67000169 1.0 67000170 0.0 67000171 0.0 67000172 0.0 67000173 0.0 67000174 1.0 67000175 0.0 67000176 0.0 67000177 0.0 67000178 1.0 67000179 1.0 67000180 0.0 67000181 0.0 67000182 0.0 67000183 1.0 67000184 0.0 67000185 0.0 67000186 0.0 67000187 0.0 67000188 1.0 67000189 0.0 67000190 1.0 67000191 0.0 67000192 0.0 67000193 0.0 67000194 1.0 67000195 0.0 67000196 0.0 67000197 0.0 67000198 1.0 67000199 0.0 67000200 1.0 67000201 1.0 67000202 0.0 67000203 0.0 67000204 1.0 67000205 0.0 67000206 1.0 67000207 0.0 67000208 0.0 67000209 0.0 67000210 0.0 67000211 0.0 67000212 0.0 67000213 0.0 67000214 1.0 67000215 0.0 67000216 0.0 67000217 1.0 67000218 1.0 67000219 0.0 67000220 0.0 67000221 1.0 67000222 1.0 67000223 0.0 67000224 1.0 67000225 0.0 67000226 0.0 67000227 1.0 67000228 0.0 67000229 0.0 67000230 1.0 67000231 0.0 67000232 0.0 67000233 0.0 67000234 0.0 67000235 0.0 67000236 0.0 67000237 1.0 67000238 0.0 67000239 1.0 67000240 1.0 67000241 0.0 67000242 1.0 67000243 1.0 67000244 0.0 67000245 1.0 67000246 0.0 67000247 1.0 67000248 0.0 67000249 0.0 67000250 1.0 67000251 0.0 67000252 0.0 67000253 0.0 67000254 0.0 67000255 0.0 67000256 0.0 67000257 0.0 67000258 0.0 67000259 0.0 67000260 0.0 67000261 0.0 67000262 1.0 67000263 0.0 67000264 0.0 67000265 0.0 67000266 0.0 67000267 0.0 67000268 0.0 67000269 0.0 67000270 0.0 67000271 1.0 67000272 1.0 67000273 0.0 67000274 0.0 67000275 0.0 67000276 0.0 67000277 0.0 67000278 0.0 67000279 1.0 67000280 1.0 67000281 0.0 67000282 0.0 67000283 1.0 67000284 0.0 67000285 0.0 67000286 1.0 67000287 1.0 67000288 0.0 67000289 1.0 67000290 0.0 67000291 0.0 67000292 0.0 67000293 1.0 67000294 0.0 67000295 0.0 67000296 1.0 67000297 0.0 67000298 0.0 67000299 1.0 67000300 0.0 67000301 0.0 67000302 0.0 67000303 0.0 67000304 0.0 67000305 0.0

In [29]:
df=pred1.join(pred2, "reviewID", "inner").join(pred3, "reviewID", "inner")

In [30]:
df.head(5)

In [31]:
df=df.withColumn("VotingPred", df['prediction_nb']+df['prediction_nn']+df['prediction_lr'])

In [32]:
sums = [F.sum(x).alias(str(x)) for x in df.columns]
d = df.select(sums).collect()[0].asDict()

In [33]:
from pyspark.sql import functions as F
df = df.withColumn("FinalPrediction", F.when((df.VotingPred>=1),1).otherwise(0))

In [34]:
display(df.select('FinalPrediction'))

FinalPrediction 0 1 1 0 1 1 0 1 0 0 0 1 1 1 0 0 0 0 1 0 1 0 1 1 1 0 0 0 1 1 0 1 1 1 0 1 0 1 0 1 0 1 1 0 0 0 0 0 1 1 0 0 0 1 1 0 0 0 1 0 0 1 0 0 1 1 1 0 1 1 1 0 0 0 0 0 0 1 0 1 1 1 1 1 1 1 0 0 1 1 0 0 1 0 0 1 1 0 1 1 0 0 0 1 0 1 1 0 1 0 1 1 1 1 0 1 1 0 0 1 0 0 0 0 1 0 1 0 0 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 1 0 1 0 0 1 1 0 0 0 1 1 1 0 1 0 0 0 1 0 0 0 0 1 0 1 1 0 0 0 1 1 0 1 1 0 0 0 1 0 1 1 0 1 1 0 0 1 1 1 1 1 1 0 0 0 1 0 1 1 1 0 1 0 1 1 1 1 0 0 0 0 0 0 0 1 1 0 0 1 0 1 0 0 0 0 1 0 0 1 1 1 1 0 1 1 1 1 0 1 0 0 0 1 0 1 0 0 0 1 0 1 0 0 1 0 1 0 0 1 1 1 0 0 1 1 0 1 0 1 1 0 1 1 1 1 0 0 1 1 0 0 0 1 0 0 0 0 1 0 1 0 0 0 0 1 0 0 0 0 1 0 0 0 1 0 1 1 0 0 1 1 0 0 1 0 1 1 0 1 1 1 0 0 0 1 1 0 0 1 0 1 1 1 1 1 0 0 0 1 0 0 1 1 1 0 1 1 1 1 0 1 0 1 0 0 0 0 0 0 1 0 1 1 1 0 1 1 1 0 1 0 0 1 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 0 1 0 0 0 0 1 0 0 1 0 0 0 1 1 0 0 0 0 0 0 1 0 0 1 1 0 0 1 0 1 1 0 0 0 1 0 1 1 0 1 1 0 0 0 0 1 1 0 1 0 1 0 0 1 1 1 0 0 0 1 1 1 0 0 0 1 0 1 0 0 1 0 1 1 0 1 0 0 0 0 0 0 0 0 1 1 1 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 1 1 1 1 1 1 1 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 1 0 0 1 0 0 0 1 1 1 0 0 1 1 0 1 0 0 1 1 1 1 0 0 0 1 0 0 1 1 0 0 1 0 0 1 0 0 0 1 0 1 0 1 0 1 1 1 0 1 1 1 0 1 0 1 1 0 0 0 1 0 0 1 0 0 1 0 0 0 0 1 1 0 0 1 0 1 0 1 1 0 0 1 1 1 1 1 1 1 1 0 1 0 1 1 0 1 1 0 1 0 0 1 1 0 1 0 0 1 1 0 1 0 1 1 1 1 1 0 1 0 0 1 1 1 0 1 0 1 1 1 1 0 0 0 1 1 0 0 0 1 0 0 0 0 0 0 0 1 0 0 1 0 0 0 1 1 1 0 1 1 0 0 1 0 0 1 0 0 0 0 0 0 0 0 1 1 0 1 1 0 0 1 0 1 0 1 0 1 0 0 0 0 1 0 0 0 0 0 0 0 1 1 1 0 1 0 1 1 0 1 0 0 0 1 0 0 1 0 0 0 1 1 1 0 0 1 0 1 0 0 0 0 0 1 0 0 0 1 0 1 1 0 1 1 1 1 0 1 0 0 0 1 1 1 0 1 0 1 0 1 0 0 0 0 1 0 1 0 1 0 1 0 0 0 0 1 0 0 1 1 1 1 0 1 0 0 0 1 1 1 1 1 0 0 0 1 1 1 1 1 1 0 0 1 1 0 1 0 0 0 0 1 0 0 0 0 1 1 0 1 0 0 0 1 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 1 1 0 1 0 0 0 0 1 1 1 1 0 0 0 1 0 1 0 0 1 0 0 0 1 1 1 0 1 1 1 0 0 1 1 0 1 0 1 0 0 0 1 1 0 1 0 0 0 1 0 1 0 1 0 0 1 1 1 0 1 0 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 0 1 1 0 1 0 1 1 0 1 0 1 1 0 0 0 0 0 0 0 1 1 1 0 0 0 1 0 0 0 0 0 Showing the first 1000 rows.